# Prediction

In [17]:
%load_ext autoreload
%autoreload 2

from collections import Counter
from hyperparameters import params as all_params
from hyperparameters import nanSet
from math import pi
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import numpy as np
import pandas as pd
import pickle
import pymongo
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import classification_report, make_scorer, accuracy_score, f1_score, precision_score, recall_score
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.neural_network import MLPClassifier, MLPRegressor
from sklearn.neighbors import KNeighborsClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC, SVR
from sklearn.tree import DecisionTreeClassifier, DecisionTreeRegressor
from sklearn.utils import shuffle
import time
from tqdm import tqdm
import warnings
warnings.filterwarnings('ignore')

import os
import json
from subprocess import call

from sklearn.externals.six import StringIO  
from IPython.display import Image  
from sklearn.tree import export_graphviz
import pydotplus

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Functions

In [8]:
targetsNames = [ 'isWinner', 'didScoreInTWP', 'goalsDiff' ] 

targets = [
    { 'name': 'isWinner', 'type': 'categorical' },
    { 'name': 'didScoreInTWP', 'type': 'categorical' },
    { 'name': 'goalsDiff', 'type': 'categorical' } 
]

algFunction = {
    'mlpC': MLPClassifier,
    'mlpR': MLPRegressor,
    'knC': KNeighborsClassifier,
    'svC': SVC,
    'svR': SVR,
    'linReg': LinearRegression,
    'rfC': RandomForestClassifier,
    'rfR': RandomForestRegressor,
    'dtC': DecisionTreeClassifier,
    'dtR': DecisionTreeRegressor
}

scoresFunction = {
    'accuracy': accuracy_score,
    'f1': f1_score,
    'precision': precision_score,
    'recall': recall_score
}

bsLabels = { x:y for x,y in [ z for z in zip([11,12,21,31,32], 
                                             ['baseline1_1', 'baseline1_2', 'baseline2_1', 'baseline3_1', 'baseline3_2']) ] }

bsForTarget = {
    0: [11, 12],
    1: [21],
    2: [31, 32]
}

scores = ['accuracy', 'f1', 'precision', 'recall']
scoresMultiCls = ['f1', 'precision', 'recall']

## Grid Search for Decision Tree

In [32]:
def GS_DT(df, targetId, colsDrop, algParams, normalize):
    
    #TRAINING-TEST SETS
    targetName = targets[targetId]['name']
    
    Xtr = pd.DataFrame(columns=df.columns) # it will store the rows of which (matchId, teamId) have a NaN value in our baselines
    Xts = pd.DataFrame(columns=df.columns) # it will store all the other rows - THAT WILL BE SPLIT
    for i, row in df.iterrows():
        if (str(int(row['matchId'])), str(int(row['teamId']))) in nanSet:
            Xtr = Xtr.append(row)
        else:
            Xts = Xts.append(row)

    ytr = Xtr[targetName] #target column from Xtr
    yts = Xts[targetName] #target column from Xts - THAT WILL BE SPLIT

    Xts, yts = shuffle(Xts, yts) #THESE WILL BE SPLIT
    X_train, X_test, y_train, y_test = train_test_split( Xts, yts, test_size=0.19 ) #SPLIT

    X_train = pd.concat([X_train, Xtr], ignore_index=True)
    y_train = np.asarray(pd.concat([y_train, ytr], ignore_index=True),dtype=np.float64)
    y_test = np.asarray(y_test, dtype=np.float64)
    
    bsArray = { k: np.asarray(X_test[bsLabels[k]], dtype=np.float64) for k in bsForTarget[targetId] }

    colsDrop = colsDrop + [ bsLabels[k] for k in bsLabels ]
    X_train = X_train.drop(targetsNames + colsDrop + ['teamId', 'matchId'], axis=1)
    X_test = X_test.drop(targetsNames + colsDrop + ['teamId', 'matchId'], axis=1)
    
    cols = X_train.columns
    
    XX = pd.concat([X_train, X_test], ignore_index=True)
    
    if normalize:
        XX = StandardScaler().fit_transform(XX)

    X_train = XX[0:len(X_train)]
    X_test = XX[len(X_train):len(X_train)+len(X_test)]
    
    #MODELS
    res = {}
    
    for i in range(2,6):
        algParams.update({ 'max_depth': [i] })
        clf = GridSearchCV(DecisionTreeClassifier(), algParams, cv=5, scoring='accuracy')
        clf.fit(X_train, y_train)
        scRes = { sc: make_scorer(scoresFunction[sc])(clf, X_test, y_test) for sc in scores }
        res.update({ i: { 'scRes': scRes, 'bestParams': clf.best_params_, 
                         'Xtrain': X_train, 'ytrain': y_train, 'Xtest': X_test, 'ytest': y_test } })
    
    return res

## Decision Tree

In [73]:
def DT(df, targetId, colsDrop, outDir, outFileName, normalize, **kwargs):
    
    #TRAINING-TEST SETS
    targetName = targets[targetId]['name']
    
    Xtr = pd.DataFrame(columns=df.columns) # it will store the rows of which (matchId, teamId) have a NaN value in our baselines
    Xts = pd.DataFrame(columns=df.columns) # it will store all the other rows - THAT WILL BE SPLIT
    for i, row in df.iterrows():
        if (str(int(row['matchId'])), str(int(row['teamId']))) in nanSet:
            Xtr = Xtr.append(row)
        else:
            Xts = Xts.append(row)

    ytr = Xtr[targetName] #target column from Xtr
    yts = Xts[targetName] #target column from Xts - THAT WILL BE SPLIT

    Xts, yts = shuffle(Xts, yts) #THESE WILL BE SPLIT
    X_train, X_test, y_train, y_test = train_test_split( Xts, yts, test_size=0.19 ) #SPLIT

    X_train = pd.concat([X_train, Xtr], ignore_index=True)
    y_train = np.asarray(pd.concat([y_train, ytr], ignore_index=True),dtype=np.float64)
    y_test = np.asarray(y_test, dtype=np.float64)
    
    bsArray = { k: np.asarray(X_test[bsLabels[k]], dtype=np.float64) for k in bsForTarget[targetId] }

    colsDrop = colsDrop + [ bsLabels[k] for k in bsLabels ]
    X_train = X_train.drop(targetsNames + colsDrop + ['teamId', 'matchId'], axis=1)
    X_test = X_test.drop(targetsNames + colsDrop + ['teamId', 'matchId'], axis=1)
    
    XX = pd.concat([X_train, X_test], ignore_index=True)
    if normalize:
        XX = StandardScaler().fit_transform(XX)

    X_train = XX[0:len(X_train)]
    X_test = XX[len(X_train):len(X_train)+len(X_test)]
    
    #MODEL CREATION
    clf = DecisionTreeClassifier(**kwargs)
    clf.fit(X_train, y_train)
    
    #RESULTS
    accuracy_ = make_scorer(scoresFunction['accuracy'])(clf, X_test, y_test)
    resDict = {'accuracy': accuracy_, 'Xtrain': X_train, 'ytrain': y_train, 'Xtest': X_test, 'ytest': y_test}
        
    #STORE
    if not os.path.exists('./{}'.format(outDir)):
        os.mkdir('./{}'.format(outDir))
    #model
    with open('./{}/{}.pkl'.format(outDir, outFileName), 'bw') as f:
        pickle.dump(clf, f)
    #tree
    cols = X_train.columns
    export_graphviz(clf, out_file='./{}/{}.dot'.format(outDir, outFileName),
                    feature_names = cols, class_names = ['0', '1'],
                    proportion = True, precision = 2, filled=True, rounded=True,
                    special_characters=True)
    call(['dot', '-Tpng', './{}/{}.dot'.format(outDir, outFileName), '-o', './{}/{}.png'.format(outDir, outFileName), '-Gdpi=1200'])
    
    #RETURN
    return {'model': clf, **resDict}
    

In [108]:
cols = ['isHome', 'meanPlayerOverall', 'meanPlayerPotential', 'meanPrevScore',
       'meanPrevScoreET', 'meanPrevScoreHT', 'meanPrevScoreP', 'numDuel',
       'numFoul', 'numFreeKick', 'numGoalkeeperLeavingLine', 'numGoalsTW',
       'numInterruption', 'numOffside', 'numOthersOnTheBall', 'numOwnGoalsTW',
       'numPass', 'numRedCard', 'numSaveAttempt', 'numSecondYellowCard',
       'numShot', 'numYellowCard', 'percBallPoss', 'percOppHalfField',
       'rateAccFreeKick', 'rateAccPass', 'rateAccShot', 'scoreTW',
       'teamPlayerank', 'teamPoints']

def saveDTplot (DT, outDir, outFileName):
    export_graphviz(DT, 
                    #out_file=dot_data,
                    out_file='./{}/{}.dot'.format(outDir, outFileName),
                    feature_names = cols,
                    class_names = ['no', 'yes'],
                    proportion = True, precision = 2,
                    filled=True, rounded=True,
                    special_characters=True)
    
    # Convert to png using system command (requires Graphviz)
    from subprocess import call
    call(['dot', '-Tpng', './{}/{}.dot'.format(outDir, outFileName), '-o', './{}/{}.png'.format(outDir, outFileName), '-Gdpi=1200'])
    
    return

## Dataframe with predicted target variables

In [102]:
cols = ['isHome', 'meanPlayerOverall', 'meanPlayerPotential', 'meanPrevScore',
       'meanPrevScoreET', 'meanPrevScoreHT', 'meanPrevScoreP', 'numDuel',
       'numFoul', 'numFreeKick', 'numGoalkeeperLeavingLine', 'numGoalsTW',
       'numInterruption', 'numOffside', 'numOthersOnTheBall', 'numOwnGoalsTW',
       'numPass', 'numRedCard', 'numSaveAttempt', 'numSecondYellowCard',
       'numShot', 'numYellowCard', 'percBallPoss', 'percOppHalfField',
       'rateAccFreeKick', 'rateAccPass', 'rateAccShot', 'scoreTW',
       'teamPlayerank', 'teamPoints']

def dfPrediction (df, inDir, clf1_fileName, clf2_fileName, save=False, outDir='', outFileName=''):
    
    #loading models
    clf1 = pickle.load(open('./{}/{}.pkl'.format(inDir, clf1_fileName), 'rb'))
    clf2 = pickle.load(open('./{}/{}.pkl'.format(inDir, clf2_fileName), 'rb'))
    
    #predict targets
    df_pred = df
    df_pred['isWinner_predicted'] = clf1.predict(df[cols]).astype(int)
    df_pred['didScoreInTWP_predicted'] = clf2.predict(df[cols]).astype(int)
    
    if save:
        df_pred.to_json('./{}/{}.json'.format(outDir, outFileName), orient='records')
    
    return df_pred

# Execution

In [ ]:
data = pd.read_json('./dataForModelsBS.json', orient='records')
colsDrop_ = ['numGoals1H', 'numGoals2H', 'numGoalsET', 'finalScore', 'numGoalsTWP', 'numOwnGoalsTWP']

***

In [53]:
algParams = {   
                'criterion': ['gini', 'entropy'],
                'splitter': ['best', 'random'],
                'min_samples_split': [2, 5, 10, 15, 30, 50],
                'max_features': [2,4,6,8,10,'sqrt', 'log2', None]
            }

GS_DT_1 = GS_DT(data, 0, colsDrop_, algParams, False)
GS_DT_2 = GS_DT(data, 1, colsDrop_, algParams, False)

algParams = {   
                'criterion': ['gini', 'entropy'],
                'splitter': ['best', 'random'],
                'min_samples_split': [.05, .10, .15, .25, .50],
                'min_samples_leaf': [.02, .05, .10, .15, .20],
                'max_features': [2,4,6,8,10,'sqrt', 'log2', None]
            }

GS_DT_1_2 = GS_DT(data, 0, colsDrop_, algParams, False)
GS_DT_2_2 = GS_DT(data, 1, colsDrop_, algParams, False)

***

In [51]:
data = pd.read_json('./dataForModelsBS.json', orient='records')
colsDrop_ = ['numGoals1H', 'numGoals2H', 'numGoalsET', 'finalScore', 'numGoalsTWP', 'numOwnGoalsTWP']
resGS = { 1: GS_DT_1, 2: GS_DT_1 }

for target in [1,2]:
    d = resGS[target]
    for depth in [2,3,4,5]:
        parms = d[depth]['bestParams']
        DT(data, target-1, colsDrop_, 'NewModels', 'DT_{}_{}'.format(target, depth), False,
           criterion=parms['criterion'], max_depth=parms['max_depth'], max_features=parms['max_features'], 
           min_samples_split=parms['min_samples_split'], splitter=parms['splitter'])
        print('target = %d - depth = %d - accuracy = %.3f' %(target, depth, d[depth]['scRes']['accuracy']))

target = 1 - depth = 4 - accuracy = 0.741
target = 2 - depth = 4 - accuracy = 0.741


In [59]:
data = pd.read_json('./dataForModelsBS.json', orient='records')
colsDrop_ = ['numGoals1H', 'numGoals2H', 'numGoalsET', 'finalScore', 'numGoalsTWP', 'numOwnGoalsTWP']
resGS = { 1: GS_DT_1_2, 2: GS_DT_1_2 }

for target in [1]:
    d = resGS[target]
    for depth in [5]:
        parms = d[depth]['bestParams']
        DT(data, target-1, colsDrop_, 'NewModels2', 'DT_{}_{}'.format(target, depth), False,
           criterion=parms['criterion'], max_depth=parms['max_depth'], max_features=parms['max_features'], 
           min_samples_split=parms['min_samples_split'], min_samples_leaf=parms['min_samples_leaf'], splitter=parms['splitter'])
        print('target = %d - depth = %d - accuracy = %.3f' %(target, depth, d[depth]['scRes']['accuracy']))

target = 1 - depth = 5 - accuracy = 0.735


In [109]:
saveDTplot(pickle.load(open('./NewModels6/DT_{}_{}_10.pkl'.format(1, 3), 'rb')), 'NewModels6', 'DT_{}_{}_yesNo'.format(1, 3))

In [110]:
Image(filename = './NewModels6/DT_1_3_yesNo.png')

In [111]:
Image(filename = './NewModels6/DT_2_3_yesNo.png')

***

In [105]:
dfResPred = dfPrediction(data, 'NewModels6', 'DT_1_3_10', 'DT_2_3_10')

In [106]:
dfResPred[]

baseline1_1  baseline1_2  baseline2_1  baseline3_1  baseline3_2  \
0             0.0          0.0          0.0         -2.0          1.0   
1             0.0          1.0          0.0          1.0          2.0   
2             0.0          1.0          0.0          2.0          2.0   
3             0.0          1.0          0.0          1.0          1.0   
4             0.0          1.0          0.0          2.0          1.0   
5             0.0          1.0          0.0          1.0          1.0   
6             0.0          1.0          0.0          1.0          1.0   
7             0.0          1.0          0.0          1.0          1.0   
8             0.0          1.0          0.0          2.0          2.0   
9             0.0          1.0          0.0          2.0          2.0   
10            0.0          1.0          0.0          1.0          2.0   
11            0.0          1.0          0.0          1.0          1.0   
12            0.0          0.0          0.0          0.0          1.0   
13            0.0          1.0          0.0          1.0          1.0   
14            0.0          0.0          0.0          2.0          2.0   
15            0.0          1.0          0.0          2.0          1.0   
16            0.0          0.0          0.0         -1.0          0.0   
17            0.0          0.0          0.0          1.0          1.0   
18            0.0          0.0          0.0         -1.0          1.0   
19            0.0          0.0          0.0          0.0          0.0   
20            0.0          0.0          0.0          0.0          0.0   
21            0.0          1.0          0.0          2.0          2.0   
22            0.0          0.0          0.0          0.0          0.0   
23            0.0          1.0          0.0          3.0          2.0   
24            0.0          1.0          0.0          2.0          1.0   
25            0.0          1.0          0.0          2.0          1.0   
26            0.0          0.0          0.0         -2.0         -1.0   
27            0.0          1.0          0.0          1.0          1.0   
28            0.0          0.0          0.0         -3.0          1.0   
29            0.0          0.0          0.0          0.0          0.0   
...           ...          ...          ...          ...          ...   
3852          0.0          NaN          0.0          NaN         -1.0   
3853          0.0          NaN          0.0          NaN          0.0   
3854          0.0          NaN          0.0          NaN          0.0   
3855          0.0          0.0          0.0         -1.0         -1.0   
3856          0.0          NaN          0.0          NaN          1.0   
3857          0.0          0.0          0.0         -1.0         -1.0   
3858          0.0          NaN          0.0          NaN         -1.0   
3859          0.0          0.0          0.0         -2.0         -2.0   
3860          NaN          NaN          NaN          NaN          NaN   
3861          NaN          NaN          NaN          NaN          NaN   
3862          0.0          NaN          0.0          NaN          2.0   
3863          0.0          NaN          0.0          NaN         -1.0   
3864          NaN          NaN          NaN          NaN          NaN   
3865          NaN          NaN          NaN          NaN          NaN   
3866          NaN          NaN          NaN          NaN          NaN   
3867          NaN          NaN          NaN          NaN          NaN   
3868          NaN          NaN          NaN          NaN          NaN   
3869          NaN          NaN          NaN          NaN          NaN   
3870          NaN          NaN          NaN          NaN          NaN   
3871          NaN          NaN          NaN          NaN          NaN   
3872          NaN          NaN          NaN          NaN          NaN   
3873          NaN          NaN          NaN          NaN          NaN   
3874          NaN          NaN          NaN          NaN        

***